In [1]:
try:
    import evidently
except:
    !pip install git+https://github.com/evidentlyai/evidently.git

In [2]:
import pandas as pd
import numpy as np

from sklearn import datasets, ensemble, model_selection

from evidently import ColumnMapping
from evidently.report import Report
from evidently.metric_preset import DataDriftPreset
from evidently.metric_preset import DataQualityPreset
from evidently.metric_preset import RegressionPreset
from evidently.metric_preset import ClassificationPreset
from evidently.metric_preset import TargetDriftPreset

In [3]:
from joblib import load

from flask import Flask, jsonify, request, jsonify, render_template
import json

from sklearn.preprocessing import LabelEncoder
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import MinMaxScaler
from sklearn.neighbors import NearestNeighbors
from sklearn.model_selection import train_test_split

from imblearn.under_sampling  import RandomUnderSampler

from lightgbm import LGBMClassifier

import warnings
warnings.filterwarnings("ignore")

# 1. Prepare Datasets and model predictions

In [4]:
data_merged=pd.read_csv('merged_data_feat_eng.csv')
data=data_merged.copy()

In [5]:
data.head()

Unnamed: 0  SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0           0      100002     1.0         Cash loans           M            N   
1           1      100003     0.0         Cash loans           F            N   
2           2      100004     0.0    Revolving loans           M            Y   
3           3      100006     0.0         Cash loans           F            N   
4           4      100007     0.0         Cash loans           M            N   

  FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  ...  \
0               Y             0          202500.0    406597.5  ...   
1               N             0          270000.0   1293502.5  ...   
2               Y             0           67500.0    135000.0  ...   
3               Y             0          135000.0    312682.5  ...   
4               Y             0          121500.0    513000.0  ...   

   PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_VERSION  \
0                                        1.052632   
1                                        1.047619   
2                                        1.333333   
3                                        1.400000   
4                                        1.129412   

   PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_NUMBER  \
0                                      10.000000   
1                                       4.666667   
2                                       2.000000   
3                                       3.166667   
4                                       6.843956   

  PREV_APPL_MEAN_POS_MEAN_DAYS_INSTALMENT  \
0                             -295.000000   
1                            -1164.333333   
2                             -754.000000   
3                             -260.666667   
4                            -1087.881319   

  PREV_APPL_MEAN_POS_MEAN_DAYS_ENTRY_PAYMENT  \
0                                -315.421053   
1                               -1171.781746   
2                                -761.666667   
3                                -285.966667   
4                               -1090.768539   

  PREV_APPL_MEAN_POS_MEAN_AMT_INSTALMENT PREV_APPL_MEAN_POS_MEAN_AMT_PAYMENT  \
0                           11559.247105                        11559.247105   
1                           78558.479286                        78558.479286   
2                            7096.155000                         7096.155000   
3                          241944.225000                       241944.225000   
4                           12122.995738                        11671.540210   

  CREDIT_INCOME_PERCENT  ANNUITY_INCOME_PERCENT  CREDIT_TERM  \
0              2.007889                0.121978     0.060749   
1              4.790750                0.132217     0.027598   
2              2.000000                0.100000     0.050000   
3              2.316167                0.219900     0.094941   
4              4.222222                0.179963     0.042623   

   DAYS_EMPLOYED_PERCENT  
0              -0.067329  
1              -0.070862  
2              -0.011814  
3              -0.159905  
4              -0.152418  

[5 rows x 194 columns]

In [6]:
data.shape

(356255, 194)

In [15]:
app_train_csv=pd.read_csv("application_train.csv")
app_train=app_train_csv.copy()

In [16]:
app_test_csv = pd.read_csv("application_test.csv")
app_test=app_test_csv.copy()

In [17]:
data_train = data[data['SK_ID_CURR'].isin(app_train.SK_ID_CURR)]
data_test = data[data['SK_ID_CURR'].isin(app_test.SK_ID_CURR)]

In [22]:
data_train=data_train.drop(['Unnamed: 0'],axis=1)

In [23]:
data_train.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0      100002     1.0         Cash loans           M            N   
1      100003     0.0         Cash loans           F            N   
2      100004     0.0    Revolving loans           M            Y   
3      100006     0.0         Cash loans           F            N   
4      100007     0.0         Cash loans           M            N   

  FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0               Y             0          202500.0    406597.5      24700.5   
1               N             0          270000.0   1293502.5      35698.5   
2               Y             0           67500.0    135000.0       6750.0   
3               Y             0          135000.0    312682.5      29686.5   
4               Y             0          121500.0    513000.0      21865.5   

   ...  PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_VERSION  \
0  ...                                        1.052632   
1  ...                                        1.047619   
2  ...                                        1.333333   
3  ...                                        1.400000   
4  ...                                        1.129412   

  PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_NUMBER  \
0                                     10.000000   
1                                      4.666667   
2                                      2.000000   
3                                      3.166667   
4                                      6.843956   

  PREV_APPL_MEAN_POS_MEAN_DAYS_INSTALMENT  \
0                             -295.000000   
1                            -1164.333333   
2                             -754.000000   
3                             -260.666667   
4                            -1087.881319   

  PREV_APPL_MEAN_POS_MEAN_DAYS_ENTRY_PAYMENT  \
0                                -315.421053   
1                               -1171.781746   
2                                -761.666667   
3                                -285.966667   
4                               -1090.768539   

  PREV_APPL_MEAN_POS_MEAN_AMT_INSTALMENT PREV_APPL_MEAN_POS_MEAN_AMT_PAYMENT  \
0                           11559.247105                        11559.247105   
1                           78558.479286                        78558.479286   
2                            7096.155000                         7096.155000   
3                          241944.225000                       241944.225000   
4                           12122.995738                        11671.540210   

   CREDIT_INCOME_PERCENT  ANNUITY_INCOME_PERCENT  CREDIT_TERM  \
0               2.007889                0.121978     0.060749   
1               4.790750                0.132217     0.027598   
2               2.000000                0.100000     0.050000   
3               2.316167                0.219900     0.094941   
4               4.222222                0.179963     0.042623   

   DAYS_EMPLOYED_PERCENT  
0              -0.067329  
1              -0.070862  
2              -0.011814  
3              -0.159905  
4              -0.152418  

[5 rows x 193 columns]

In [24]:
data_train.shape

(307511, 193)

In [25]:
data_test=data_test.drop(['Unnamed: 0'],axis=1)

In [26]:
data_test.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
307511      100001     NaN         Cash loans           F            N   
307512      100005     NaN         Cash loans           M            N   
307513      100013     NaN         Cash loans           M            Y   
307514      100028     NaN         Cash loans           F            N   
307515      100038     NaN         Cash loans           M            Y   

       FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
307511               Y             0          135000.0    568800.0   
307512               Y             0           99000.0    222768.0   
307513               Y             0          202500.0    663264.0   
307514               Y             2          315000.0   1575000.0   
307515               N             1          180000.0    625500.0   

        AMT_ANNUITY  ...  PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_VERSION  \
307511      20560.5  ...                                        1.250000   
307512      17370.0  ...                                        1.111111   
307513      69777.0  ...                                        1.050926   
307514      49018.5  ...                                        1.038889   
307515      32067.0  ...                                        1.000000   

       PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_NUMBER  \
307511                                      2.500000   
307512                                      5.000000   
307513                                      6.027778   
307514                                     17.595238   
307515                                      6.500000   

       PREV_APPL_MEAN_POS_MEAN_DAYS_INSTALMENT  \
307511                            -1664.000000   
307512                             -586.000000   
307513                             -854.833333   
307514                             -944.964286   
307515                             -622.000000   

       PREV_APPL_MEAN_POS_MEAN_DAYS_ENTRY_PAYMENT  \
307511                               -1679.500000   
307512                                -609.555556   
307513                                -867.592593   
307514                                -949.814286   
307515                                -634.250000   

       PREV_APPL_MEAN_POS_MEAN_AMT_INSTALMENT  \
307511                            7312.725000   
307512                            6240.205000   
307513                           16349.077917   
307514                            7836.897982   
307515                           11100.337500   

       PREV_APPL_MEAN_POS_MEAN_AMT_PAYMENT  CREDIT_INCOME_PERCENT  \
307511                         7312.725000               4.213333   
307512                         6240.205000               2.250182   
307513                        13702.794792               3.275378   
307514                         7557.738339               5.000000   
307515                        11100.337500               3.475000   

        ANNUITY_INCOME_PERCENT  CREDIT_TERM  DAYS_EMPLOYED_PERCENT  
307511                0.152300     0.036147               0.121044  
307512                0.175455     0.077973               0.247398  
307513                0.344578     0.105202               0.222477  
307514                0.155614     0.031123               0.133515  
307515                0.178150     0.051266               0.168021  

[5 rows x 193 columns]

In [27]:
data_train.columns

Index(['SK_ID_CURR', 'TARGET', 'NAME_CONTRACT_TYPE', 'CODE_GENDER',
       'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'CNT_CHILDREN', 'AMT_INCOME_TOTAL',
       'AMT_CREDIT', 'AMT_ANNUITY',
       ...
       'PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_VERSION',
       'PREV_APPL_MEAN_POS_MEAN_NUM_INSTALMENT_NUMBER',
       'PREV_APPL_MEAN_POS_MEAN_DAYS_INSTALMENT',
       'PREV_APPL_MEAN_POS_MEAN_DAYS_ENTRY_PAYMENT',
       'PREV_APPL_MEAN_POS_MEAN_AMT_INSTALMENT',
       'PREV_APPL_MEAN_POS_MEAN_AMT_PAYMENT', 'CREDIT_INCOME_PERCENT',
       'ANNUITY_INCOME_PERCENT', 'CREDIT_TERM', 'DAYS_EMPLOYED_PERCENT'],
      dtype='object', length=193)

In [28]:
#Feature engineering fonction 

def features_engineering(data_train, data_test):

    # Cette fonction regroupe toutes les opérations de features engineering
    # mises en place sur les sets train & test

    #############################################
    # LABEL ENCODING
    #############################################
    # Create a label encoder object
    le = LabelEncoder()
    le_count = 0

    # Iterate through the columns
    for col in data_train:
        if data_train[col].dtype == 'object':
            # If 2 or fewer unique categories
            if len(list(data_train[col].unique())) <= 2:
                # Train on the training data
                le.fit(data_train[col])
                # Transform both training and testing data
                data_train[col] = le.transform(data_train[col])
                data_test[col] = le.transform(data_test[col])
                
                # Keep track of how many columns were label encoded
                le_count += 1

    ############################################
    # ONE HOT ENCODING
    ############################################
    # one-hot encoding of categorical variables
    data_train = pd.get_dummies(data_train)
    data_test = pd.get_dummies(data_test)

    train_labels = data_train['TARGET']
    # Align the training and testing data, keep only columns present in both dataframes
    data_train, data_test = data_train.align(data_test, join = 'inner', axis = 1)
    # Add the target back in
    data_train['TARGET'] = train_labels

    return data_train, data_test

# Entraînement du modèle
#@app.route("/init_model", methods=["GET"])
def init_model(data_train,data_test):
    
    # On prépare les données
    df_train, df_test = features_engineering(data_train, data_test)
    df_train=df_train.drop(labels="Unnamed: 0",axis=1)
    df_test=df_test.drop(labels="Unnamed: 0",axis=1)

    print("Features engineering done")
    return df_train,df_test

In [37]:
def preprocesseur(df_train, df_test):
    
    # Cette fonction permet d'imputer les valeurs manquantes dans
    # chaque dataset et aussi d'appliquer un MinMaxScaler

    # Drop the target from the training data
    if "TARGET" in df_train:
        train = df_train.drop(columns = ["TARGET"])
        df_test = df_test.drop(columns = ["TARGET"])
    else:
        train = df_train.copy()
        
    # Feature names
    features = list(train.columns)


    # Median imputation of missing values
    imputer = SimpleImputer(strategy = 'median')

    # Scale each feature to 0-1
    scaler = MinMaxScaler(feature_range = (0, 1))


    # Fit on the training data
    imputer.fit(train)

    # Transform both training and testing data
    train = imputer.transform(train)
    test = imputer.transform(df_test)

    # Repeat with the scaler
    scaler.fit(train)
    train = scaler.transform(train)
    test = scaler.transform(test)
    
    return train, test

In [30]:
def data_resampler(df_train, target):

    rsp = RandomUnderSampler()
    X_rsp, y_rsp = rsp.fit_resample(df_train, target["TARGET"])

    return X_rsp, y_rsp

In [31]:
# Models 
def entrainement_LightBoost(X, y):

    # Configuration de la meilleure itération trouvée par le RandomizeSearchCV
    # Optimized n_estimator=1144
    clf_lgbm = LGBMClassifier(colsample_bytree=0.600170715692459, 
                              device='gpu',
                              learning_rate=0.02975841167356727, 
                              max_depth=7, 
                              n_estimators=600,
                              reg_lambda=2.156064880286573, 
                              subsample=0.629809210489369)

    clf_lgbm.fit(X, y)

    return clf_lgbm

def entrainement_knn(df):

    print("En cours...")
    knn = NearestNeighbors(n_neighbors=10, algorithm='auto').fit(df)

    return knn

In [33]:
# On prépare les données
df_train, df_test = features_engineering(data_train, data_test)

In [38]:
# On fait le préprocessing des données
df_train, df_test = preprocesseur(df_train, df_test)

In [39]:
train = df_train.copy()

In [40]:
test = df_test.copy()

In [41]:
# On fait un resampling des données d'entraînement
X, y = data_resampler(df_train, data_train)

In [80]:
X

array([[0.2337468 , 1.        , 0.        , ..., 0.        , 1.        ,
        0.        ],
       [0.47718335, 0.        , 0.        , ..., 0.        , 1.        ,
        0.        ],
       [0.34199852, 0.        , 1.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.99991579, 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.99993825, 0.        , 0.        , ..., 0.        , 0.        ,
        1.        ],
       [0.99999719, 0.        , 0.        , ..., 0.        , 1.        ,
        0.        ]])

In [43]:
clf_lgbm = entrainement_LightBoost(X, y)
print("Training LightBoost done")

Training LightBoost done


In [44]:
knn = entrainement_knn(df_train)
print("Training knn done")

En cours...
Training knn done


In [19]:
data_client=test.copy()

In [20]:
prediction = clf_lgbm.predict_proba(data_client)

# 2. Datasets ref et cur

In [113]:
dat_train,dat_test=features_engineering(data_train, data_test)

In [114]:
dat_train.dtypes

SK_ID_CURR                           int64
TARGET                             float64
NAME_CONTRACT_TYPE                   int32
FLAG_OWN_CAR                         int32
FLAG_OWN_REALTY                      int32
                                    ...   
WALLSMATERIAL_MODE_Panel              bool
WALLSMATERIAL_MODE_Stone, brick       bool
WALLSMATERIAL_MODE_Wooden             bool
EMERGENCYSTATE_MODE_No                bool
EMERGENCYSTATE_MODE_Yes               bool
Length: 311, dtype: object

In [116]:
for col in dat_train:
    dat_train[col]=dat_train[col].fillna(dat_train[col].median())

In [105]:
#dat_train=dat_train.fillna(median)

In [117]:
dat_train=dat_train.dropna()

In [118]:
dat_train=dat_train.astype(int) 

In [119]:
dat_train

SK_ID_CURR  TARGET  NAME_CONTRACT_TYPE  FLAG_OWN_CAR  FLAG_OWN_REALTY  \
0           100002       1                   0             0                1   
1           100003       0                   0             0                0   
2           100004       0                   1             1                1   
3           100006       0                   0             0                1   
4           100007       0                   0             0                1   
...            ...     ...                 ...           ...              ...   
307506      456251       0                   0             0                0   
307507      456252       0                   0             0                1   
307508      456253       0                   0             0                1   
307509      456254       1                   0             0                1   
307510      456255       0                   0             0                0   

        CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0                  0            202500      406597        24700   
1                  0            270000     1293502        35698   
2                  0             67500      135000         6750   
3                  0            135000      312682        29686   
4                  0            121500      513000        21865   
...              ...               ...         ...          ...   
307506             0            157500      254700        27558   
307507             0             72000      269550        12001   
307508             0            153000      677664        29979   
307509             0            171000      370107        20205   
307510             0            157500      675000        49117   

        AMT_GOODS_PRICE  ...  HOUSETYPE_MODE_terraced house  \
0                351000  ...                              0   
1               1129500  ...                              0   
2                135000  ...                              0   
3                297000  ...                              0   
4                513000  ...                              0   
...                 ...  ...                            ...   
307506           225000  ...                              0   
307507           225000  ...                              0   
307508           585000  ...                              0   
307509           319500  ...                              0   
307510           675000  ...                              0   

        WALLSMATERIAL_MODE_Block  WALLSMATERIAL_MODE_Mixed  \
0                              0                         0   
1                              1                         0   
2                              0                         0   
3                              0                         0   
4                              0                         0   
...                          ...                       ...   
307506                         0                         0   
307507                         0                         0   
307508                         0                         0   
307509                         0                         0   
307510                         0                         0   

        WALLSMATERIAL_MODE_Monolithic  WALLSMATERIAL_MODE_Others  \
0                                   0                          0   
1                                   0                          0   
2                                   0                          0   
3                                   0                          0   
4                                   0                          0   
...                               ...                        ...   
307506                              0                          0   
307507                              0                          0   
307508                              0                          0   
307509                              0           

In [120]:
import re
dat_train = dat_train.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))

In [121]:
data_ref = dat_train.sample(n=200, replace=False)
data_cur = dat_train.sample(n=300, replace=False)

In [122]:
data_label_ref = data_ref.copy(deep=True)
data_label_cur = data_cur.copy(deep=True)

In [123]:
model = LGBMClassifier(colsample_bytree=0.600170715692459, learning_rate=0.02975841167356727,max_depth=7,n_estimators=600,reg_lambda=2.156064880286573, subsample=0.629809210489369)
model.feature_names = list(dat_train.columns.values)
model.fit(data_ref[dat_train.columns.tolist()], data_ref.TARGET)

LGBMClassifier(colsample_bytree=0.600170715692459,
               learning_rate=0.02975841167356727, max_depth=7, n_estimators=600,
               reg_lambda=2.156064880286573, subsample=0.629809210489369)

In [124]:
data_ref['prediction'] = model.predict_proba(data_ref[dat_train.columns.tolist()])[:, 1]
data_cur['prediction'] = model.predict_proba(data_cur[dat_train.columns.tolist()])[:, 1]

In [125]:
data_label_ref['prediction'] = model.predict(data_label_ref[dat_train.columns.tolist()])
data_label_cur['prediction'] = model.predict(data_label_cur[dat_train.columns.tolist()])

In [126]:
data_drift_report = Report(metrics=[
    DataDriftPreset(num_stattest='ks', cat_stattest='psi', num_stattest_threshold=0.2, cat_stattest_threshold=0.2),
])

data_drift_report.run(reference_data=data_ref, current_data=data_cur)
data_drift_report

In [127]:
data_drift_report.save_html('data_drift_report.html')

In [133]:
binary_cat_target_drift_report = Report(metrics=[
    TargetDriftPreset(cat_stattest='psi'),
])

binary_cat_target_drift_report.run(reference_data=data_label_ref, current_data=data_label_cur)
binary_cat_target_drift_report

In [134]:
binary_cat_target_drift_report.save_html('binary_cat_target_drift_report.html')

In [135]:
prob_binary_cat_target_drift_report = Report(metrics=[
    TargetDriftPreset(num_stattest='ks', cat_stattest='psi'),
])

prob_binary_cat_target_drift_report.run(reference_data=data_ref, current_data=data_cur)
prob_binary_cat_target_drift_report

In [136]:
prob_binary_cat_target_drift_report.save_html('prob_binary_cat_target_drift_report.html')